In [1]:
# Importing required libraries
import sys
# adding to the path variables the one folder higher (locally, not changing system variables)
sys.path.append("..")

import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import mlflow

from prophet import Prophet
from prophet.plot import plot_plotly, plot_components_plotly
from prophet.diagnostics import performance_metrics, cross_validation
from sklearn.metrics import mean_squared_error, r2_score, confusion_matrix
from datetime import datetime

import warnings
warnings.filterwarnings('ignore')

from modeling.config import EXPERIMENT_NAME
TRACKING_URI = open("../.mlflow_uri").read().strip()

In [42]:
data = pd.read_csv("../data/merged_final_1h.csv")

In [3]:
data

dt_start_utc  windspeed_ms  epex_da_de_eur_mwh  \
0      2019-01-01 00:00:00       13.7925               10.07   
1      2019-01-01 01:00:00       14.3600               -4.08   
2      2019-01-01 02:00:00       15.0180               -9.91   
3      2019-01-01 03:00:00       14.8220               -7.41   
4      2019-01-01 04:00:00       14.5930              -12.55   
...                    ...           ...                 ...   
15331  2020-09-30 19:00:00        6.1635               49.92   
15332  2020-09-30 20:00:00        5.9385               42.79   
15333  2020-09-30 21:00:00        6.0630               35.02   
15334  2020-09-30 22:00:00        6.2825               34.40   
15335  2020-09-30 23:00:00        6.3625               34.00   

       solar_mw_fiftyhertz  solar_mw_tennet  solar_mw_amprion  \
0                      0.0             0.00               0.0   
1                      0.0             0.00               0.0   
2                      0.0             0.00               0.0   
3                      0.0             0.00               0.0   
4                      0.0             0.00               0.0   
...                    ...              ...               ...   
15331                  0.0             0.03               0.0   
15332                  0.0             0.05               0.0   
15333                  0.0             0.05               0.0   
15334                  0.0             0.06               0.0   
15335                  0.0             0.01               0.0   

       solar_mw_transnetbw  solar_mw_nrv   fc_da  fc_load_50H  ...  \
0                      0.0          0.00  29.730       6150.5  ...   
1                      0.0          0.00  26.050       6029.0  ...   
2                      0.0          0.00  23.760       6057.0  ...   
3                      0.0          0.00  20.950       6122.5  ...   
4                      0.0          0.00  15.770       6152.0  ...   
...                    ...           ...     ...          ...  ...   
15331                  0.0          0.03  53.555      11108.5  ...   
15332                  0.0          0.05  46.200      10454.5  ...   
15333                  0.0          0.05  40.030       9635.5  ...   
15334                  0.0          0.06  37.970       9068.0  ...   
15335                  0.0          0.01  36.020       8696.0  ...   

       offshore_mw_nrv  onshore_mw_fiftyhertz  onshore_mw_tennet  \
0              5684.34                9231.31           11624.89   
1              5334.19               10012.16           12762.32   
2              5278.54               10852.08           13988.91   
3              5160.90               11761.89           14809.73   
4              5001.96               13125.93           15131.73   
...                ...                    ...                ...   
15331          4756.97                 651.60            3648.29   
15332          5196.46                 707.77            3953.82   
15333          5339.31                 779.20            3957.25   
15334          5396.54                 847.60            4031.58   
15335          5342.51                1010.84            4171.43   

       onshore_mw_amprion  onshore_mw_transnetbw  onshore_mw_nrv  month  \
0                 3039.50                 105.45        24001.15      1   
1                 3576.50                 112.04        26463.02      1   
2                 4094.75                 164.29        29100.03      1   
3                 4685.25                 226.52        31483.39      1   
4                 5024.50                 315.82        33597.98      1   
...                   ...                    ...             ...    ...   
15331             1620.00                 179.00         6098.89      9   
15332             1977.75                 259.00         6898.34      9   
15333             2123.75                 284.25         7144.45      9   
15334             2152.50                 326.25        

In [43]:
# set timestamp as index
data['dt_start_utc'] = pd.to_datetime(data['dt_start_utc'])

In [44]:
df = data[['dt_start_utc', 'imbalance_price_target', 'fc_da', 'fc_load_DE', 'windspeed_ms', 'fc_onshore_DE', 'fc_offshore_DE', 'fc_solar_DE', 'weekday', 'hour', 'month']]

In [45]:
df.rename(columns={'dt_start_utc': 'ds', 'imbalance_price_target': 'y'}, inplace=True)

In [46]:
df

ds       y   fc_da  fc_load_DE  windspeed_ms  \
0     2019-01-01 00:00:00  -3.465  29.730     41218.5       13.7925   
1     2019-01-01 01:00:00  -3.735  26.050     40139.0       14.3600   
2     2019-01-01 02:00:00  -9.250  23.760     39917.0       15.0180   
3     2019-01-01 03:00:00  11.355  20.950     40282.0       14.8220   
4     2019-01-01 04:00:00  -4.925  15.770     40528.0       14.5930   
...                   ...     ...     ...         ...           ...   
15331 2020-09-30 19:00:00  16.450  53.555     56709.0        6.1635   
15332 2020-09-30 20:00:00  26.050  46.200     53241.0        5.9385   
15333 2020-09-30 21:00:00  56.265  40.030     49149.0        6.0630   
15334 2020-09-30 22:00:00  41.335  37.970     46540.0        6.2825   
15335 2020-09-30 23:00:00  29.340  36.020     44828.0        6.3625   

       fc_onshore_DE  fc_offshore_DE  fc_solar_DE  weekday  hour  month  
0            20618.5          5021.0          0.0        1     0      1  
1            22352.0          5028.0          0.0        1     1      1  
2            24035.0          4978.0          0.0        1     2      1  
3            25475.0          4908.0          0.0        1     3      1  
4            26538.5          4884.0          0.0        1     4      1  
...              ...             ...          ...      ...   ...    ...  
15331         6282.0          3545.5          0.0        2    19      9  
15332         7379.0          3931.0          0.0        2    20      9  
15333         8190.0          4156.5          0.0        2    21      9  
15334         7684.5          4768.0          0.0        2    22      9  
15335         7943.5          4479.0          0.0        2    23      9  

[15336 rows x 11 columns]

### Modeling

In [47]:
def train_test_split(df):
    n = int(len(df)*0.7)
    train, test = df.iloc[:n], df.iloc[n:]
    return train,test

In [48]:
train, test = train_test_split(df)

In [10]:
m = Prophet()
m.fit(train)

INFO:prophet:Disabling yearly seasonality. Run prophet with yearly_seasonality=True to override this.


Initial log joint probability = -80.7587


    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
      99       23394.5    0.00469751       540.884           1           1      132   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     199       23399.8     0.0010439       158.242           1           1      252   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     299       23401.8   0.000360909       167.136      0.1318      0.1318      372   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     319       23402.3    8.8458e-05           286   1.819e-07       0.001      438  LS failed, Hessian reset 
     399       23403.2   0.000192169       78.8162           1           1      537   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     499       23403.6     8.024e-05       66.4058           1           1      6

In [11]:
future = m.make_future_dataframe(periods=24, freq='H')

In [12]:
forecast = m.predict(future)
forecast[['ds', 'yhat', 'yhat_lower', 'yhat_upper']].tail()

ds       yhat  yhat_lower  yhat_upper
10754 2020-03-24 02:00:00  14.905135  -36.425138   64.493452
10755 2020-03-24 03:00:00  17.108067  -36.730175   69.354387
10756 2020-03-24 04:00:00  21.009152  -31.624680   73.766672
10757 2020-03-24 05:00:00  25.048038  -28.094793   75.698114
10758 2020-03-24 06:00:00  27.599341  -24.381001   78.616752

In [13]:
# forecasts plot
plot_plotly(m, forecast)

In [14]:
# components
plot_components_plotly(m, forecast)

#for i in range(len(test_2019)):
forecasts_1h = []
test_imb = test
train_imb = train
print(len(test_imb))
for i in range(len(test_imb)):
    train_imb = pd.concat([train_imb, pd.DataFrame(test_imb.iloc[i]).T])
    m3 = Prophet(daily_seasonality=True, weekly_seasonality=True, yearly_seasonality=True)
    m3.add_seasonality(name='half day', period=0.5, fourier_order=5)
    m3.add_country_holidays(country_name='DE')
    m3.add_regressor('fc_da')
    m3.add_regressor('fc_load_DE')
    m3.add_regressor('windspeed_ms')
    m3.add_regressor('fc_onshore_DE')
    m3.add_regressor('fc_offshore_DE')
    m3.fit(train_imb)
    future3 = m3.make_future_dataframe(periods=1, freq='H')
    future3['fc_da'] = df[df['ds'] <= future3.iloc[-1]['ds']]['fc_da']
    future3['fc_load_DE'] = df[df['ds'] <= future3.iloc[-1]['ds']]['fc_load_DE']
    future3['windspeed_ms'] = df[df['ds'] <= future3.iloc[-1]['ds']]['windspeed_ms']
    future3['fc_onshore_DE'] = df[df['ds'] <= future3.iloc[-1]['ds']]['fc_onshore_DE']
    future3['fc_offshore_DE'] = df[df['ds'] <= future3.iloc[-1]['ds']]['fc_offshore_DE']
    forecast3 = m3.predict(future3)
    forecast_1h = forecast['yhat'][0]
    print(i)
    forecasts_1h.append(forecast_1h)

In [15]:
#for i in range(len(test_2019)):
forecasts_6h = []
test_imb = test
train_imb = train
print(len(test_imb))
for i in range(0,len(test_imb),6):
    train_imb = pd.concat([train_imb, test_imb.iloc[i:i+6]], axis=0)
    m3 = Prophet(daily_seasonality=True, weekly_seasonality=True, yearly_seasonality=True)
    m3.add_seasonality(name='half day', period=0.5, fourier_order=5)
    m3.add_country_holidays(country_name='DE')
    m3.add_regressor('fc_da')
    m3.add_regressor('fc_load_DE')
    m3.add_regressor('windspeed_ms')
    m3.add_regressor('fc_onshore_DE')
    m3.add_regressor('fc_offshore_DE')
    m3.fit(train_imb)
    future3 = m3.make_future_dataframe(periods=6, freq='H')
    future3['fc_da'] = df[df['ds'] <= future3.iloc[-1]['ds']]['fc_da']
    future3['fc_load_DE'] = df[df['ds'] <= future3.iloc[-1]['ds']]['fc_load_DE']
    future3['windspeed_ms'] = df[df['ds'] <= future3.iloc[-1]['ds']]['windspeed_ms']
    future3['fc_onshore_DE'] = df[df['ds'] <= future3.iloc[-1]['ds']]['fc_onshore_DE']
    future3['fc_offshore_DE'] = df[df['ds'] <= future3.iloc[-1]['ds']]['fc_offshore_DE']
    forecast3 = m3.predict(future3)
    forecast_6h = forecast3['yhat'][0:6]
    print(f"{i} / {len(test_imb)}")
    forecasts_6h.append(forecast_6h)

4601
Initial log joint probability = -39.9673
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
      99       23894.2   0.000155222       128.755           1           1      115   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     192       23894.3   5.35456e-05       126.906   6.982e-07       0.001      279  LS failed, Hessian reset 
     199       23894.3   7.90866e-05       74.8704           1           1      289   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     267       23894.3   0.000239781       160.808   3.921e-06       0.001      424  LS failed, Hessian reset 
     299       23894.3    2.4152e-05       54.1161      0.3342      0.8008      461   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     309       23894.3   5.07249e-06       50.1007       0.412           1      478   
Optimization ter

ValueError: Found NaN in column 'fc_da'

In [22]:
results = []

In [23]:
for element in forecasts_6h:
    for i in np.array(element):
        results.append(i)

In [24]:
results

[12.478858981425336,
 10.011844345786674,
 8.070727849248811,
 4.253050274688626,
 0.4815352787687317,
 -1.9192773185018588,
 12.790195646750362,
 10.329848463291889,
 8.218768028239804,
 4.460844010734224,
 0.8070410564733557,
 -1.700300916817298,
 13.557163635945725,
 11.065191905334864,
 8.885357585601255,
 5.110167736055896,
 1.3925470014368457,
 -1.1005414169375207,
 12.3982021786052,
 9.967673334568968,
 7.861075644592404,
 4.134349574854312,
 0.3307080632549777,
 -2.261748133763465,
 12.580201791381505,
 10.051362895789548,
 8.02424432747426,
 4.189668380146895,
 0.553321717207492,
 -2.0798758264641997,
 12.586431992639753,
 10.020978438377643,
 7.98882032058523,
 4.114074266837381,
 0.5468628534784692,
 -2.1102506081646233,
 12.577387016369588,
 10.044932271025672,
 7.9803720551275745,
 4.1471556976696995,
 0.5568830563317775,
 -2.0488751542616406,
 13.205970502176356,
 10.633323398439018,
 8.603303088916384,
 4.786701281221845,
 1.1458178385435573,
 -1.5378145849380118,
 12.83

In [49]:
pred_df = test

In [50]:
pred_df

ds        y   fc_da  fc_load_DE  windspeed_ms  \
10735 2020-03-23 07:00:00   56.745  36.630     66652.5        5.6435   
10736 2020-03-23 08:00:00 -368.605  33.440     67207.0        6.1285   
10737 2020-03-23 09:00:00  -88.885  28.440     67850.0        7.5570   
10738 2020-03-23 10:00:00   85.235  26.930     68998.5        7.5515   
10739 2020-03-23 11:00:00   40.500  24.840     68291.5        7.1915   
...                   ...      ...     ...         ...           ...   
15331 2020-09-30 19:00:00   16.450  53.555     56709.0        6.1635   
15332 2020-09-30 20:00:00   26.050  46.200     53241.0        5.9385   
15333 2020-09-30 21:00:00   56.265  40.030     49149.0        6.0630   
15334 2020-09-30 22:00:00   41.335  37.970     46540.0        6.2825   
15335 2020-09-30 23:00:00   29.340  36.020     44828.0        6.3625   

       fc_onshore_DE  fc_offshore_DE  fc_solar_DE  weekday  hour  month  
10735        12547.5          4829.5      15329.0        0     7      3  
10736        12805.5          4745.5      23007.0        0     8      3  
10737        13815.5          4530.0      28286.0        0     9      3  
10738        14044.5          4238.5      30951.0        0    10      3  
10739        13507.5          3997.0      31585.5        0    11      3  
...              ...             ...          ...      ...   ...    ...  
15331         6282.0          3545.5          0.0        2    19      9  
15332         7379.0          3931.0          0.0        2    20      9  
15333         8190.0          4156.5          0.0        2    21      9  
15334         7684.5          4768.0          0.0        2    22      9  
15335         7943.5          4479.0          0.0        2    23      9  

[4601 rows x 11 columns]

In [36]:
results_series = pd.Series(results)

In [38]:
type(results_series)

pandas.core.series.Series

In [54]:
results_series

0       12.478859
1       10.011844
2        8.070728
3        4.253050
4        0.481535
          ...    
4585     8.228109
4586     5.696150
4587     1.410581
4588    -2.790310
4589    -2.906905
Length: 4590, dtype: float64

In [52]:
pred_df['pred_6h'] = results_series

In [55]:
pred_df.drop('pred_6h', axis=1, inplace=True)

In [61]:
pred_df = pred_df.reset_index()

In [62]:
pred_df['pred_6h'] = results_series

In [63]:
pred_df

index                  ds        y   fc_da  fc_load_DE  windspeed_ms  \
0     10735 2020-03-23 07:00:00   56.745  36.630     66652.5        5.6435   
1     10736 2020-03-23 08:00:00 -368.605  33.440     67207.0        6.1285   
2     10737 2020-03-23 09:00:00  -88.885  28.440     67850.0        7.5570   
3     10738 2020-03-23 10:00:00   85.235  26.930     68998.5        7.5515   
4     10739 2020-03-23 11:00:00   40.500  24.840     68291.5        7.1915   
...     ...                 ...      ...     ...         ...           ...   
4596  15331 2020-09-30 19:00:00   16.450  53.555     56709.0        6.1635   
4597  15332 2020-09-30 20:00:00   26.050  46.200     53241.0        5.9385   
4598  15333 2020-09-30 21:00:00   56.265  40.030     49149.0        6.0630   
4599  15334 2020-09-30 22:00:00   41.335  37.970     46540.0        6.2825   
4600  15335 2020-09-30 23:00:00   29.340  36.020     44828.0        6.3625   

      fc_onshore_DE  fc_offshore_DE  fc_solar_DE  weekday  hour  month  \
0           12547.5          4829.5      15329.0        0     7      3   
1           12805.5          4745.5      23007.0        0     8      3   
2           13815.5          4530.0      28286.0        0     9      3   
3           14044.5          4238.5      30951.0        0    10      3   
4           13507.5          3997.0      31585.5        0    11      3   
...             ...             ...          ...      ...   ...    ...   
4596         6282.0          3545.5          0.0        2    19      9   
4597         7379.0          3931.0          0.0        2    20      9   
4598         8190.0          4156.5          0.0        2    21      9   
4599         7684.5          4768.0          0.0        2    22      9   
4600         7943.5          4479.0          0.0        2    23      9   

        pred_6h  
0     12.478859  
1     10.011844  
2      8.070728  
3      4.253050  
4      0.481535  
...         ...  
4596        NaN  
4597        NaN  
4598        NaN  
4599        NaN  
4600        NaN  

[4601 rows x 13 columns]

In [65]:
pred_df = pred_df[['ds', 'y', 'pred_6h']]

In [68]:
pred_df = pred_df.dropna()

In [69]:
pred_df

ds        y    pred_6h
0    2020-03-23 07:00:00   56.745  12.478859
1    2020-03-23 08:00:00 -368.605  10.011844
2    2020-03-23 09:00:00  -88.885   8.070728
3    2020-03-23 10:00:00   85.235   4.253050
4    2020-03-23 11:00:00   40.500   0.481535
...                  ...      ...        ...
4585 2020-09-30 08:00:00   29.380   8.228109
4586 2020-09-30 09:00:00   33.490   5.696150
4587 2020-09-30 10:00:00   64.305   1.410581
4588 2020-09-30 11:00:00   20.590  -2.790310
4589 2020-09-30 12:00:00   20.590  -2.906905

[4590 rows x 3 columns]

In [71]:
pred_df.to_csv("../data/results_6h.csv")

In [80]:
#for i in range(len(test_2019)):
forecasts_1h_uni = []
test_imb = test
train_imb = train
print(len(test_imb))
for i in range(len(test_imb)):
    train_imb = pd.concat([train_imb, test_imb.iloc[[i]]], axis=0)
    m4 = Prophet(daily_seasonality=True, weekly_seasonality=True, yearly_seasonality=True)
    m4.fit(train_imb)
    future4 = m4.make_future_dataframe(periods=1, freq='H')
    forecast4 = m4.predict(future4)
    forecast_1h = forecast4['yhat'][0]
    print(f"{i} / {len(test_imb)}")
    forecasts_1h_uni.append(forecast_1h)

4601
Initial log joint probability = -37.5173
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
      99       23608.9   7.37463e-05       81.9531      0.4286      0.4286      121   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     134         23609   0.000125603       234.208    9.23e-07       0.001      197  LS failed, Hessian reset 
     186       23609.4   0.000104137       185.738   5.464e-07       0.001      301  LS failed, Hessian reset 
     199       23609.5   0.000491274       314.156           1           1      316   
    Iter      log prob        ||dx||      ||grad||       alpha      alpha0  # evals  Notes 
     266       23609.7   6.28138e-07        91.852      0.4002      0.9756      396   
Optimization terminated normally: 
  Convergence detected: relative gradient magnitude is below tolerance
0 / 4601
Initial log joint probability = -948.845
    Iter      log prob        ||dx||   

KeyboardInterrupt: 

In [81]:
 forecasts_1h_uni

[31.661674399683115,
 32.978957504660826,
 32.9011791603509,
 31.620669118712293,
 32.09678124007327,
 32.26192751634031,
 31.316023244930363,
 33.2433107446834,
 32.66648531221566,
 31.83707993336256,
 31.90678297952661,
 32.884032289633076,
 33.19085231100019,
 32.13423549679365,
 32.184341046849894,
 32.3083406783896,
 32.16196486925119,
 32.48527817587165,
 32.48046170115586,
 32.15844244812561,
 31.61499362364044,
 32.5099100252774,
 32.93612899667048,
 32.7107061439097,
 31.788792669113242,
 32.909755006542525,
 32.203083423194926,
 32.813545654016686,
 32.99264231595057,
 32.849567818431495,
 32.700295794591455,
 32.594920356458395,
 32.992993454069534,
 32.14973885571519,
 32.15314958744706,
 32.789134972573535,
 32.91423520851474,
 31.98741322876411,
 32.70160980002695,
 33.03190762752448,
 32.768007522802485,
 32.43932065850884,
 32.61277627377627,
 32.344501143069984,
 32.276996295814456,
 32.15540055620678,
 32.441486175724314,
 32.34590465236343,
 32.701293220022436,
 32.7

In [82]:
forecasts_series = pd.Series(forecasts_1h_uni)

In [85]:
test2 = test.reset_index()

In [86]:
test2['pred_1h_uni'] = forecasts_series

In [88]:
test2.drop("pred_6h", axis=1, inplace=True)

In [89]:
test2

index                  ds        y   fc_da  fc_load_DE  windspeed_ms  \
0     10735 2020-03-23 07:00:00   56.745  36.630     66652.5        5.6435   
1     10736 2020-03-23 08:00:00 -368.605  33.440     67207.0        6.1285   
2     10737 2020-03-23 09:00:00  -88.885  28.440     67850.0        7.5570   
3     10738 2020-03-23 10:00:00   85.235  26.930     68998.5        7.5515   
4     10739 2020-03-23 11:00:00   40.500  24.840     68291.5        7.1915   
...     ...                 ...      ...     ...         ...           ...   
4596  15331 2020-09-30 19:00:00   16.450  53.555     56709.0        6.1635   
4597  15332 2020-09-30 20:00:00   26.050  46.200     53241.0        5.9385   
4598  15333 2020-09-30 21:00:00   56.265  40.030     49149.0        6.0630   
4599  15334 2020-09-30 22:00:00   41.335  37.970     46540.0        6.2825   
4600  15335 2020-09-30 23:00:00   29.340  36.020     44828.0        6.3625   

      fc_onshore_DE  fc_offshore_DE  fc_solar_DE  weekday  hour  month  \
0           12547.5          4829.5      15329.0        0     7      3   
1           12805.5          4745.5      23007.0        0     8      3   
2           13815.5          4530.0      28286.0        0     9      3   
3           14044.5          4238.5      30951.0        0    10      3   
4           13507.5          3997.0      31585.5        0    11      3   
...             ...             ...          ...      ...   ...    ...   
4596         6282.0          3545.5          0.0        2    19      9   
4597         7379.0          3931.0          0.0        2    20      9   
4598         8190.0          4156.5          0.0        2    21      9   
4599         7684.5          4768.0          0.0        2    22      9   
4600         7943.5          4479.0          0.0        2    23      9   

      pred_1h_uni  
0       31.661674  
1       32.978958  
2       32.901179  
3       31.620669  
4       32.096781  
...           ...  
4596          NaN  
4597          NaN  
4598          NaN  
4599          NaN  
4600          NaN  

[4601 rows x 13 columns]

In [91]:
test2[['ds', 'y', 'pred_1h_uni']]

ds        y  pred_1h_uni
0    2020-03-23 07:00:00   56.745    31.661674
1    2020-03-23 08:00:00 -368.605    32.978958
2    2020-03-23 09:00:00  -88.885    32.901179
3    2020-03-23 10:00:00   85.235    31.620669
4    2020-03-23 11:00:00   40.500    32.096781
...                  ...      ...          ...
4596 2020-09-30 19:00:00   16.450          NaN
4597 2020-09-30 20:00:00   26.050          NaN
4598 2020-09-30 21:00:00   56.265          NaN
4599 2020-09-30 22:00:00   41.335          NaN
4600 2020-09-30 23:00:00   29.340          NaN

[4601 rows x 3 columns]

In [92]:
test2.to_csv("../data/forecasts_1h_1f_prophet.csv")